In [1]:
import matplotlib.pyplot as plt
%matplotlib inline
import os
import json
import pickle
#import torch
import numpy as np
import re
from tqdm.notebook import tqdm
from sklearn.utils import shuffle
from transformers import AutoTokenizer
import warnings
warnings.filterwarnings("ignore")

None of PyTorch, TensorFlow >= 2.0, or Flax have been found. Models won't be available and only tokenizers, configuration and file/data utilities can be used.


In [2]:
model_type = 'SZTAKI-HLT/hubert-base-cc' # bert-base-multilingual-cased, SZTAKI-HLT/hubert-base-cc


data_path = f"C:/Users/pozmanreka/PycharmProjects/test/venv/src/neural_punctuator/data/"
os.makedirs(data_path + model_type, exist_ok=True)
file_path = data_path + "hu.txt"

with open(file_path, 'r', encoding='utf-8') as f:
    text = f.readlines()
    
len(text), text[1]

(477905, 'Fordította:\n')

In [3]:
from collections import OrderedDict

text = list(OrderedDict.fromkeys(text))
len(text)

244027

In [4]:
from sklearn.utils import shuffle

text = shuffle(text, random_state=0)

text[1]

'Ott maradtak.\n'

In [5]:
tokenizer = AutoTokenizer.from_pretrained(model_type)

In [6]:
def clean_text(text):
    text = text.replace('!', '.')
    text = text.replace(':', ',')
    text = text.replace('--', ',')
    text = text.replace(' – ', ', ')
    text = text.replace('- ', '')
    text = text.replace('_', ' ')
    text = text.replace('\\', ' per ')

    
    reg = "(?<=[a-zA-Z])-(?=[a-zA-Z]{2,})"
    r = re.compile(reg, re.DOTALL)
    text = r.sub(' ', text)
    
    text = text.replace('-', ',')
    text = text.replace(';', '.')
    text = text.replace(' ,', ',')
    text = text.replace('(', ', ')
    text = text.replace(')', ', ')
    
    text = text.replace('...', '')
    text = text.replace('.\"', ',')
    text = text.replace('"', ',')
    
    text = re.sub(r'\s-\s', ' , ', text)

    text = re.sub(r'--\s?--', '', text)   
    
    text = re.sub(r',\s?,', ', ', text)
    text = re.sub(r'\.[\s+.]+', '. ', text)
    
    text = re.sub(r',\s?,', ',', text)
    
    text = re.sub(r'\s+', ' ', text)
    
    remove_space_before = [',', '?', '.', '!', '\n']
    for c in remove_space_before:
        text = text.replace(' ' + c, c)
    
    text = re.sub(r',\s+[\.,\s]+', ', ', text)
    text = re.sub(r'\.\s+[\.,\s]+', '. ', text)
    text = re.sub(r'\.[\.,]+', '.', text)
    text = re.sub(r'\,[\.,]+', ',', text)
    text = re.sub(r'\,[\.,]+', ',', text)
    text = text.lstrip('.,?')
    
    
    text = re.sub(r'(\w)(\n)', r'\1.\2', text)
    text = re.sub(r'\n.\n', r'\n', text) 
    
    return text.strip().lower()

In [7]:
text = [clean_text(t) for t in text]
text = [t for t in text if len(t) > 0]
len(text), text[1]

(244007, 'ott maradtak.')

In [8]:
# ' '.join(text[train_n:train_n+valid_n])

In [9]:
text[2]

'én nem ezt látom.'

In [10]:
for i, t in enumerate(text):
    if 'egyéniségek' in t:
        print(i, t)

5992 a képességünk, hogy egyéniségek legyünk, a lelkünk ami különbözővé tesz tőlük.
51852 képességünk van arra, hogy egyéniségek legyünk, és a lelkünk az, ami megkülönböztet minket tőlük.
95765 a képességünk, hogy egyéniségek legyünk, a lelkünk amiben különbözünk tőlük.
142319 képességünk van arra, hogy egyéniségek legyünk és a lelkünk az, ami megkülönböztet minket tőlük.


In [11]:
tokenizer.encode(".?,")

[2, 4575, 8308, 3576, 3]

In [12]:
target_token2id = {t: tokenizer.encode(t)[-2] for t in ".?,"}
target_token2id

{'.': 4575, '?': 8308, ',': 3576}

In [13]:
target_ids = list(target_token2id.values())
target_ids

[4575, 8308, 3576]

In [14]:
id2target = {
    0: 0,
    -1: -1,
}
for i, ti in enumerate(target_ids):
    id2target[ti] = i+1
target2id = {value: key for key, value in id2target.items()}

def create_target(text):
    encoded_words, targets = [], []
    
    words = text.split(' ')

    for word in tqdm(words):
        target = 0
        for target_token, target_id in target_token2id.items():
            if word.endswith(target_token):
                word = word.rstrip(target_token)
                target = id2target[target_id]

        encoded_word = tokenizer.encode(word, add_special_tokens=False)
        
        for w in encoded_word:
            encoded_words.append(w)
        for _ in range(len(encoded_word)-1):
            targets.append(-1)
        targets.append(target)
        #print([tokenizer._convert_id_to_token(ew) for ew in encoded_word], target)
        assert(len(encoded_word)>0)

    return encoded_words, targets

In [15]:
train_n = 210_000
valid_n = 20_000
test_n = 8_000

train_text = ' '.join(text[:train_n])
valid_text = ' '.join(text[train_n:train_n+valid_n])
test_text = ' '.join(text[train_n+valid_n:test_n+valid_n+train_n])

len(train_text.split(' ')), len(valid_text.split(' ')), len(test_text.split(' '))

(1034550, 98641, 39510)

In [16]:
len(text) - train_n - valid_n

14007

In [17]:
train_text.split(' ')[5-5:5+5]

['az',
 'öreg',
 'halász,',
 'és',
 'a',
 'tenger.',
 'ott',
 'maradtak.',
 'én',
 'nem']

In [18]:
train_tokens, train_targets = create_target(train_text)
valid_tokens, valid_targets = create_target(valid_text)
test_tokens, test_targets = create_target(test_text)

  0%|          | 0/1034550 [00:00<?, ?it/s]

  0%|          | 0/98641 [00:00<?, ?it/s]

  0%|          | 0/39510 [00:00<?, ?it/s]

In [19]:
# For backward campatibility
train_tokens, train_targets = [train_tokens], [train_targets]
valid_tokens, valid_targets = [valid_tokens], [valid_targets]
test_tokens, test_targets = [test_tokens], [test_targets]

In [20]:
os.makedirs(data_path + model_type, exist_ok=True)
with open(data_path + f'{model_type}/train_data.pkl', 'wb') as f:
    pickle.dump((train_tokens, train_targets), f)
with open(data_path + f'{model_type}/valid_data.pkl', 'wb') as f:
    pickle.dump((valid_tokens, valid_targets), f)
with open(data_path + f'{model_type}/test_data.pkl', 'wb') as f:
    pickle.dump((test_tokens, test_targets), f)

In [21]:
from collections import Counter

for ds in (train_targets, valid_targets, test_targets):
    c = Counter((t for targets in ds for t in targets))
    print('\t'.join([str(c[i]) for i in (1,2,3,0,-1)]))

160720	35034	110271	728525	408680
15219	3410	10473	69539	38775
6044	1408	4180	27878	15591


In [22]:
e = []
i = 0

raw_words = valid_text.split(' ')

for te, ta in zip(valid_tokens[0], valid_targets[0]):
    if ta == -1:
        e.append(te)
    else:
        e.append(te)
        print(f"{tokenizer.decode(e):15}\t{tokenizer.decode(target2id[ta]):10}\t{raw_words[i]}")
        e = []
        i += 1

nem            	[PAD]     	nem
meztelen       	[PAD]     	meztelen
férfi          	[PAD]     	férfi
alakjában      	[PAD]     	alakjában
jelent         	[PAD]     	jelent
meg            	[PAD]     	meg
előtted        	?         	előtted?
legalábbis     	[PAD]     	legalábbis
hallott        	[PAD]     	hallott
róla           	[PAD]     	róla
mindenki       	,         	mindenki,
fiúk           	.         	fiúk.
stark          	[PAD]     	stark
fehérororszország	[PAD]     	fehérororszország
déli           	[PAD]     	déli
határán        	,         	határán,
egy            	[PAD]     	egy
bázison        	[PAD]     	bázison
van            	.         	van.
fel            	[PAD]     	fel
foglak         	[PAD]     	foglak
ébreszteni     	.         	ébreszteni.
egyébként      	,         	egyébként,
a              	[PAD]     	a
terv           	[PAD]     	terv
nem            	[PAD]     	nem
változik       	.         	változik.
buffy          	[PAD]     	buffy
2x15, phases   	,         	2x15,phase

kiiktató       	?         	kiiktató?
de             	[PAD]     	de
mi             	?         	mi?
ráadásul       	,         	ráadásul,
ez             	[PAD]     	ez
egy            	[PAD]     	egy
alku           	.         	alku.
a              	[PAD]     	a
haverjaid      	[PAD]     	haverjaid
kötélre        	[PAD]     	kötélre
juttatnak      	,         	juttatnak,
ők             	[PAD]     	ők
meg            	[PAD]     	meg
kidumálják     	[PAD]     	kidumálják
magukat        	.         	magukat.
akkor          	[PAD]     	akkor
visszamehetsz  	[PAD]     	visszamehetsz
az             	[PAD]     	az
iskolába       	.         	iskolába.
eljött         	[PAD]     	eljött
a              	[PAD]     	a
nap            	,         	nap,
amikor         	[PAD]     	amikor
kurt           	[PAD]     	kurt
végre          	[PAD]     	végre
úgy            	[PAD]     	úgy
döntött        	,         	döntött,
hogy           	[PAD]     	hogy
kiszáll        	[PAD]     	kiszáll
ebből          	[PAD]     	e

semmi          	[PAD]     	semmi
rosszat        	[PAD]     	rosszat
nem            	[PAD]     	nem
tett           	[PAD]     	tett
neked          	.         	neked.
ezért          	,         	ezért,
most           	[PAD]     	most
itt            	[PAD]     	itt
maradsz        	[PAD]     	maradsz
iskola         	[PAD]     	iskola
után           	.         	után.
igen           	,         	igen,
nagyon         	[PAD]     	nagyon
is             	.         	is.
ez             	[PAD]     	ez
folyamatban    	[PAD]     	folyamatban
lévő           	[PAD]     	lévő
nyomozás       	.         	nyomozás.
azok           	[PAD]     	azok
helyett        	[PAD]     	helyett
ír             	[PAD]     	ír
leveleket      	,         	leveleket,
akik           	[PAD]     	akik
nem            	[PAD]     	nem
tudnak         	[PAD]     	tudnak
írni           	.         	írni.
felveszem      	,         	felveszem,
és             	[PAD]     	és
elmegyünk      	[PAD]     	elmegyünk
bevásárolni    	,         	bev

tanácsteremben 	[PAD]     	tanácsteremben
láttam         	.         	láttam.
datte          	,         	datte,
datte          	,         	datte,
datte          	,         	datte,
datte          	,         	datte,
de             	[PAD]     	de
mégis          	,         	mégis,
de             	[PAD]     	de
mégis          	,         	mégis,
tsubasa        	[PAD]     	tsubasa
hiroge         	[PAD]     	hiroge
futari         	[PAD]     	futari
de             	[PAD]     	de
kitárjuk       	[PAD]     	kitárjuk
szárnyainkat   	[PAD]     	szárnyainkat
és             	.         	és.
egy            	[PAD]     	egy
golyó          	[PAD]     	golyó
van            	.         	van.
de             	[PAD]     	de
megbaszom      	[PAD]     	megbaszom
az             	[PAD]     	az
anyját         	[PAD]     	anyját
együtt         	[PAD]     	együtt
vagyunk        	[PAD]     	vagyunk
mint           	[PAD]     	mint
régen          	[PAD]     	régen
varjak         	[PAD]     	varjak
csapata        	.       

egy            	[PAD]     	egy
cellában       	,         	cellában,
egy            	[PAD]     	egy
olyan          	[PAD]     	olyan
bűntettért     	,         	bűntettért,
amit           	[PAD]     	amit
maga           	[PAD]     	maga
követett       	[PAD]     	követett
el             	.         	el.
kik            	[PAD]     	kik
maguk          	?         	maguk?
befejeznéd     	,         	befejeznéd,
hogy           	[PAD]     	hogy
ilyenkor       	[PAD]     	ilyenkor
is             	[PAD]     	is
csak           	[PAD]     	csak
a              	[PAD]     	a
hasadra        	[PAD]     	hasadra
gondolsz       	?         	gondolsz?
még            	[PAD]     	még
hanno, t       	[PAD]     	hanno,t
is             	.         	is.
mostantól      	[PAD]     	mostantól
én             	[PAD]     	én
diktálom       	[PAD]     	diktálom
a              	[PAD]     	a
szabályokat    	.         	szabályokat.
minek          	[PAD]     	minek
köszönhetem    	[PAD]     	köszönhetem
a              	[PAD] 

...

miért          	[PAD]     	miért
lőtted         	[PAD]     	lőtted
le             	[PAD]     	le
rózsit         	?         	rózsit?
most           	[PAD]     	most
kérdeztem      	?         	kérdeztem?
akkor          	[PAD]     	akkor
nem            	[PAD]     	nem
is             	[PAD]     	is
olvasta        	[PAD]     	olvasta
a              	[PAD]     	a
könyvét        	,         	könyvét,
a              	[PAD]     	a
varjú          	[PAD]     	varjú
csapatot       	.         	csapatot.
hadd           	[PAD]     	hadd
lássák         	[PAD]     	lássák
a              	[PAD]     	a
hölgyek        	,         	hölgyek,
hogy           	[PAD]     	hogy
ő              	[PAD]     	ő
egy            	[PAD]     	egy
gayle          	.         	gayle.
ahogy          	[PAD]     	ahogy
gondoltam      	,         	gondoltam,
a              	[PAD]     	a
sok            	[PAD]     	sok
cigaretta      	.         	cigaretta.
elengedem      	.         	elengedem.
kansasban      	[PAD]     	kansasban
van 

csinálta       	[PAD]     	csinálta
ezt            	[PAD]     	ezt
számdékosan    	[PAD]     	számdékosan
tönkretette    	[PAD]     	tönkretette
a              	[PAD]     	a
rádiót         	.         	rádiót.
39             	[PAD]     	39
pont           	,         	pont,
14             	[PAD]     	14
gólpassz       	.         	gólpassz.
vulcani        	[PAD]     	vulcani
kal            	[PAD]     	kal
toh            	.         	toh.
a              	[PAD]     	a
nők            	[PAD]     	nők
nem            	[PAD]     	nem
házasodnak     	[PAD]     	házasodnak
egymással      	[PAD]     	egymással
te             	[PAD]     	te
gyökér         	.         	gyökér.
ennyi          	[PAD]     	ennyi
készpénzt      	[PAD]     	készpénzt
cipelni        	[PAD]     	cipelni
is             	[PAD]     	is
kész           	[PAD]     	kész
idegbaj        	.         	idegbaj.
róla           	[PAD]     	róla
fogunk         	[PAD]     	fogunk
elnevezni      	,         	elnevezni,
mi             	[PAD]    

a              	[PAD]     	a
számot         	.         	számot.
megy           	[PAD]     	megy
egy            	[PAD]     	egy
kocsi          	[PAD]     	kocsi
este           	[PAD]     	este
contentionbe   	,         	contentionbe,
azzal          	[PAD]     	azzal
átküldöm       	.         	átküldöm.
na             	,         	na,
húzzál         	[PAD]     	húzzál
innen          	.         	innen.
azt            	[PAD]     	azt
kérdezném      	,         	kérdezném,
hogy           	[PAD]     	hogy
elmegyünk, e   	[PAD]     	elmegyünk,e
valahová       	?         	valahová?
hadd           	[PAD]     	hadd
daráljak       	.         	daráljak.
intelligensnek 	?         	intelligensnek?
oh             	,         	oh,
menjen         	[PAD]     	menjen
már            	.         	már.
soha           	[PAD]     	soha
nem            	[PAD]     	nem
is             	[PAD]     	is
volt           	.         	volt.
van            	[PAD]     	van
másik          	[PAD]     	másik
potts          	[PAD] 

ha             	[PAD]     	ha
belehal        	[PAD]     	belehal
a              	[PAD]     	a
visszavágásba  	[PAD]     	visszavágásba
ellenük        	.         	ellenük.
véletlenül     	[PAD]     	véletlenül
a              	[PAD]     	a
szádra         	[PAD]     	szádra
jött           	,         	jött,
én             	[PAD]     	én
küldtem        	.         	küldtem.
öröm           	[PAD]     	öröm
magával        	[PAD]     	magával
üzletet        	[PAD]     	üzletet
kötni          	.         	kötni.
valahogy       	[PAD]     	valahogy
nagyon         	[PAD]     	nagyon
nem            	[PAD]     	nem
passzol        	[PAD]     	passzol
a              	[PAD]     	a
logikád        	[PAD]     	logikád
12, 50         	,         	12,50,
nyomj          	[PAD]     	nyomj
enter, t       	.         	enter,t.
kérem          	,         	kérem,
kommentálja    	[PAD]     	kommentálja
az             	[PAD]     	az
ítéletet       	.         	ítéletet.
lsmerem        	[PAD]     	lsmerem
a              

beszéltünk     	[PAD]     	beszéltünk
a              	[PAD]     	a
fizetségről    	.         	fizetségről.
szerintem      	[PAD]     	szerintem
nincs          	[PAD]     	nincs
benne          	.         	benne.
a              	[PAD]     	a
rakományunk    	[PAD]     	rakományunk
közt           	[PAD]     	közt
szaglászott    	.         	szaglászott.
nem            	[PAD]     	nem
úgy            	[PAD]     	úgy
tűnik          	.         	tűnik.
most           	[PAD]     	most
hallgasson     	[PAD]     	hallgasson
meg            	,         	meg,
aztán          	[PAD]     	aztán
majd           	[PAD]     	majd
mondja         	[PAD]     	mondja
el             	[PAD]     	el
az             	[PAD]     	az
embereknek     	[PAD]     	embereknek
is             	.         	is.
ellenkezik     	[PAD]     	ellenkezik
az             	[PAD]     	az
iskolai        	[PAD]     	iskolai
házirenddel    	.         	házirenddel.
a              	[PAD]     	a
másikon        	[PAD]     	másikon
piktogrammok   	

In [23]:
print(tokenizer.decode(valid_tokens[0]))

nem meztelen férfi alakjában jelent meg előtted legalábbis hallott róla mindenki fiúk stark fehérororszország déli határán egy bázison van fel foglak ébreszteni egyébként a terv nem változik buffy 2x15, phases kaptam egy fuvart és azt sem tudjuk hogy biztonságosan tárolják, e szorosra csináld te mit csináltál volna ekkora viharban most nem beszélhetek róla byron ó hallottam a magyarázatodat meg minden de az a helyzet hogy nem áll szándékomban választani bánt valami én ezt választottam volt egy srác st joe ban missouri ban valamikor de én attól félek mi történik önnel ha nem gondoskodnak magáról 80 % szóval az egész hiábavaló volt nem kell elhinni tizenkettő és egynegyed az élet megy tovább nem győzheted le van zárka a hajón rájöttem hogy nem mindíg teheted vagy mondhatod amit akarsz kapjunk be együtt valamit mit írt le melyekkel szabadon szárnyalhatott volna a tenger felett vagy indul a kamat heti 5 % mike kontójára miért ájultál el hogy tudott levetkőzni és megszökni az asztal alatt v

In [24]:
' '.join(text[train_n:train_n+valid_n])

"nem meztelen férfi alakjában jelent meg előtted? legalábbis hallott róla mindenki, fiúk. stark fehérororszország déli határán, egy bázison van. fel foglak ébreszteni. egyébként, a terv nem változik. buffy 2x15,phases, kaptam egy fuvart és azt sem tudjuk, hogy biztonságosan tárolják,e. szorosra csináld. te mit csináltál volna ekkora viharban? most nem beszélhetek róla, byron. ó hallottam a magyarázatodat, meg minden, de az a helyzet, hogy nem áll szándékomban választani. bánt valami? én ezt választottam. volt egy srác st. joe ban, missouri ban valamikor. de én attól félek, mi történik önnel, ha nem gondoskodnak magáról. 80 %. szóval az egész hiábavaló volt? nem kell elhinni. tizenkettő és egynegyed. az élet megy tovább. nem győzheted le. van zárka a hajón? rájöttem, hogy nem mindíg teheted vagy mondhatod, amit akarsz. kapjunk be együtt valamit. mit írt le? melyekkel szabadon szárnyalhatott volna a tenger felett. vagy indul a kamat, heti 5 %, mike kontójára. miért ájultál el? hogy tudot